In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
!git clone https://github.com/keenanpepper/self-ablating-transformers

Cloning into 'self-ablating-transformers'...
remote: Enumerating objects: 138, done.
remote: Counting objects: 100% (56/56), done.
remote: Compressing objects: 100% (33/33), done.
remote: Total 138 (delta 28), reused 42 (delta 23), pack-reused 82 (from 1)
Receiving objects: 100% (138/138), 89.77 MiB | 38.35 MiB/s, done.
Resolving deltas: 100% (67/67), done.


In [3]:
!git config --global user.email "keenanpepper@gmail.com"
!git config --global user.name "Keenan Pepper"

In [4]:
cd self-ablating-transformers/

/content/self-ablating-transformers


In [5]:
!pip install -r requirements.txt

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 8.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 527.3/527.3 kB 36.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.3/8.3 MB 64.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.9/294.9 kB 23.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 49.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 174.8/174.8 kB 15.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.5/9.5 MB 73.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 739.7/739.7 kB 52.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 12.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 18.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.4/42.4 kB 4.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 41.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 311.4/

In [73]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import datasets
from tqdm.notebook import tqdm
import numpy as np
import wandb

import plotly.express as px

In [7]:
from model.gpt_neo import GPTNeoWithSelfAblation, soft_top_k
from model.config import GPTNeoWithSelfAblationConfig, TrainingConfig, WandBConfig

In [8]:
ds = datasets.load_dataset("tdooms/TinyStories")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Generating train split:   0%|          | 0/1798254 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/16384 [00:00<?, ? examples/s]

In [9]:
from utils import prepare_data

In [10]:
data, tokenizer = prepare_data(separator_token="<|endoftext|>")
print(f"Processed data shape: {data.shape}")
print(f"First 10 tokens: {data[:10]}")
print(f"Last 10 tokens: {data[-10:]}")

# Decode a small portion to verify
sample = data[:10000]
decoded = tokenizer.decode(sample.tolist())
print("\nSample decoded text:")
print(decoded[:5000] + "...")  # Print first 500 characters

Processing tdooms/TinyStories dataset...


Tokenizing the dataset (num_proc=8):   0%|          | 0/1798254 [00:00<?, ? examples/s]

Writing train.bin:   0%|          | 0/1024 [00:00<?, ?it/s]

Dataset processed and saved to train.bin
Processed data shape: (396967656,)
First 10 tokens: [ 8888    11 19919   373   845  6568    13   679   373  1016]
Last 10 tokens: [  262 25103 12023   290  8359   257 12625  8073    13 50256]

Sample decoded text:
Today, Tommy was very excited. He was going flying with his mom and dad to a special place. There was a big green flag waving in the wind when they arrived. Tommy was so happy to see it. 

He hopped out of the car and ran up to the flag. He couldn't believe how big it was! He wanted to reach out and touch it. His mom said he could and Tommy smiled.

He waved his little arms, trying to make the flag move. But the wind was too strong. His dad said, "Let me help you, Tommy." He reached out and grabbed the green flag and waved it back and forth. 

Now it was Tommy's turn! He clapped his hands and laughed as he tried to move the flag. He waved it for a long time until he was too tired to do it anymore. The big green flag was so exciting to 

In [11]:
prepare_data(split="validation", output_file="validation.bin")

Processing tdooms/TinyStories dataset...


Tokenizing the dataset (num_proc=8):   0%|          | 0/16384 [00:00<?, ? examples/s]

Writing validation.bin:   0%|          | 0/1024 [00:00<?, ?it/s]

Dataset processed and saved to validation.bin


(memmap([ 7454,  2402,   257, ..., 20567,    13, 50256], dtype=uint16),
 <Encoding 'gpt2'>)

In [12]:
class BatchGenerator:
    def __init__(self, data_file, block_size, batch_size, device):
        self.data_file = data_file
        self.block_size = block_size
        self.batch_size = batch_size
        self.device = torch.device(device)
        self.device_type = 'cuda' if 'cuda' in self.device.type else 'cpu'

    def get_batch(self, shifted=True):
        # We recreate np.memmap every batch to avoid a memory leak, as per
        # https://stackoverflow.com/questions/45132940/numpy-memmap-memory-usage-want-to-iterate-once/61472122#61472122
        data = np.memmap(self.data_file, dtype=np.uint16, mode='r')

        # Generate random starting indices
        ix = torch.randint(len(data) - self.block_size, (self.batch_size,))

        shift = 1 if shifted else 0
        # Create input and target tensors
        x = torch.stack([torch.from_numpy((data[i:i+self.block_size]).astype(np.int64)) for i in ix])
        y = torch.stack([torch.from_numpy((data[i+shift:i+shift+self.block_size]).astype(np.int64)) for i in ix])

        if self.device_type == 'cuda':
            # Pin arrays x,y, which allows us to move them to GPU asynchronously (non_blocking=True)
            x, y = x.pin_memory().to(self.device, non_blocking=True), y.pin_memory().to(self.device, non_blocking=True)
        else:
            x, y = x.to(self.device), y.to(self.device)

        return x, y

In [13]:
class LossEstimator:
    def __init__(self, model, train_batch_gen, val_batch_gen, eval_iters):
        self.model = model
        self.train_batch_gen = train_batch_gen
        self.val_batch_gen = val_batch_gen
        self.eval_iters = eval_iters

    def estimate_loss(self):
        stat_names = ["loss", "L_base", "L_ablated", "attention_ablation_mask_density", "neuron_ablation_mask_density"]
        out = {}
        for stat in stat_names:
            out[stat] = {}
        self.model.eval()
        with torch.inference_mode():
            for split, batch_gen in [('train', self.train_batch_gen), ('val', self.val_batch_gen)]:
                stats = {}
                for stat in stat_names:
                    stats[stat] = torch.zeros(self.eval_iters)
                for k in tqdm(range(self.eval_iters)):
                    X, Y = batch_gen.get_batch()
                    ret = self.model(X, Y)
                    for stat in stat_names:
                        stats[stat][k] = ret[stat].item()
                for stat in stat_names:
                    out[stat][split] = stats[stat].mean()
        self.model.train()
        return out

    def estimate_loss_pretrainedformat(self):
        out = {}
        self.model.eval()
        with torch.inference_mode():
            for split, batch_gen in [('train', self.train_batch_gen), ('val', self.val_batch_gen)]:
                losses = torch.zeros(self.eval_iters)
                for k in tqdm(range(self.eval_iters)):
                    X, Y = batch_gen.get_batch(shifted=False)
                    ret = self.model(X, labels=Y)
                    losses[k] = ret["loss"].item()
                out[split] = losses.mean()
        self.model.train()
        return out

In [14]:
wandb.login()

wandb: Using wandb-core as the SDK backend. Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

In [15]:
def train_gptneo(model, config, wandb_config):
    train_batch_gen = BatchGenerator(config.train_file, config.block_size, config.batch_size, config.device)
    val_batch_gen = BatchGenerator(config.val_file, config.block_size, config.batch_size, config.device)
    loss_estimator = LossEstimator(model, train_batch_gen, val_batch_gen, config.eval_iters)

    model.to(device)

    optimizer = optim.AdamW(model.parameters(), lr=config.learning_rate, weight_decay=config.weight_decay)
    scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=config.num_batches)
    assert config.lr_schedule == "CosineAnnealing", "Other LR schedules not implemented"

    best_val_loss = float('inf')

    wandb_run = wandb.init(
        project="gpt-neo-self-ablation",
        config=wandb_config
        )

    for iteration in tqdm(range(config.num_batches)):
        model.train()

        # Get batch
        x, y = train_batch_gen.get_batch()

        # Forward pass
        loss = model(x, targets=y)["loss"]

        # Backward pass
        optimizer.zero_grad()
        loss.backward()

        if config.max_grad_norm:
            nn.utils.clip_grad_norm_(model.parameters(), config.max_grad_norm)

        optimizer.step()
        scheduler.step()

        # Logging
        if (iteration + 1) % config.log_interval == 0:
            stats = loss_estimator.estimate_loss()
            print(f"Iteration {iteration}: train loss {stats['loss']['train']:.4f}, val loss {stats['loss']['val']:.4f}")
            print(f"train L_base {stats['L_base']['train']:.4f}, val L_base {stats['L_base']['val']:.4f}")
            print(f"train L_ablated {stats['L_ablated']['train']:.4f}, val L_ablated {stats['L_ablated']['val']:.4f}")
            print(f"train attention ablation mask density {stats['attention_ablation_mask_density']['train']:.4f}, val {stats['attention_ablation_mask_density']['val']:.4f}")
            print(f"train neuron ablation mask density {stats['neuron_ablation_mask_density']['train']:.4f}, val {stats['neuron_ablation_mask_density']['val']:.4f}")
            print(f"The current learning rate: {optimizer.param_groups[0]['lr']:.4f}")
            wandb.log(stats | {"iteration": iteration, "current_learning_rate": optimizer.param_groups[0]['lr']})

            # Save best model
            if stats['loss']['val'] < best_val_loss:
                best_val_loss = stats['loss']['val']
                torch.save(model.state_dict(), config.save_path)
                print(f"New best model saved to {config.save_path}")

    print("Training completed!")

In [17]:
device = "cuda" if torch.cuda.is_available() else "cpu"

model_config = GPTNeoWithSelfAblationConfig(d_model=128, max_position_embeddings=256)
model = GPTNeoWithSelfAblation(model_config)

training_config = TrainingConfig(batch_size=48, num_batches=200000, learning_rate=0.002, save_path="/content/drive/MyDrive/best_model_20240915.pt")

wandb_config = WandBConfig(model_config, training_config,
                           dataset_name="TinyStories",
                           ablation_mask_level="overall",
                           ablation_processing="soft-top-K-version-1",
                           reconstruction_loss=None)

train_gptneo(model, training_config, wandb_config)

  0%|          | 0/200000 [00:00<?, ?it/s]

  0%|          | 0/100 [00:00<?, ?it/s]

  0%|          | 0/100 [00:00<?, ?it/s]

Iteration 999: train loss 5.0880, val loss 5.0792
train L_base 4.6213, val L_base 4.6133
train L_ablated 4.6668, val L_ablated 4.6585
train attention ablation mask density 0.0625, val 0.0625
train neuron ablation mask density 0.0156, val 0.0156
The current learning rate: 0.0020
New best model saved to /content/drive/MyDrive/best_model_20240915.pt


  0%|          | 0/100 [00:00<?, ?it/s]

...

  0%|          | 0/100 [00:00<?, ?it/s]

Iteration 198999: train loss 2.1764, val loss 2.1889
train L_base 1.9402, val L_base 1.9516
train L_ablated 2.3621, val L_ablated 2.3727
train attention ablation mask density 0.0625, val 0.0625
train neuron ablation mask density 0.0156, val 0.0156
The current learning rate: 0.0000


  0%|          | 0/100 [00:00<?, ?it/s]

  0%|          | 0/100 [00:00<?, ?it/s]

Iteration 199999: train loss 2.1762, val loss 2.1881
train L_base 1.9401, val L_base 1.9511
train L_ablated 2.3610, val L_ablated 2.3698
train attention ablation mask density 0.0625, val 0.0625
train neuron ablation mask density 0.0156, val 0.0156
The current learning rate: 0.0000
Training completed!


In [20]:
torch.save(model.state_dict(), "best_model.pt")

In [ ]:
config = GPTNeoWithSelfAblationConfig(d_model=128, max_position_embeddings=256)
model = GPTNeoWithSelfAblation(config)
model.load_state_dict(torch.load("best_model.pt"))
model.to(device)

<ipython-input-143-b14ef4e554fd>:3: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



GPTNeoWithSelfAblation(
  (transformer): ModuleDict(
    (wte): Embedding(50257, 128)
    (wpe): Embedding(256, 128)
    (h): ModuleList(
      (0-7): 8 x GPTNeoBlockWithSelfAblation(
        (ln_1): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (attn): AttentionWithSelfAblation(
          (attention): ModuleDict(
            (k_proj): Linear(in_features=128, out_features=128, bias=False)
            (v_proj): Linear(in_features=128, out_features=128, bias=False)
            (q_proj): Linear(in_features=128, out_features=128, bias=False)
            (out_proj): Linear(in_features=128, out_features=128, bias=True)
          )
        )
        (ln_2): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (mlp): MLPWithSelfAblation(
          (c_fc): Linear(in_features=128, out_features=512, bias=True)
          (c_proj): Linear(in_features=512, out_features=128, bias=True)
          (act): NewGELUActivation()
        )
      )
    )
    (ln_f): LayerNorm((128,), 

In [43]:
tokenizer.decode(model.generate(tokenizer.encode("Tim and Lily went to the park. Tim found an interesting rock and gave it to"), 100, temperature=0.01, ablated=False))

'Tim and Lily went to the park. Tim found an interesting rock and gave it to Lily. Lily was so happy to have found a new rock. She put it on her wrist and went home. Timmy was very happy to have found the rock.<|endoftext|>Once upon a time, there was a little girl named Lily. She loved to play outside in the sunshine. One day, she saw a big, scary dog. The dog was barking and running away. Lily was scared and ran away.\n\nAs she walked, she saw a big dog. The dog was barking and'

In [44]:
tokenizer.decode(model.generate(tokenizer.encode("Tim and Lily went to the park. Lily found an interesting rock and gave it to"), 100, temperature=0.01, ablated=False))

'Tim and Lily went to the park. Lily found an interesting rock and gave it to Timmy. Timmy was so happy and said, "Thank you, Lily! You are the best!"\n\nLily and Timmy played on the swings and the slide. They had so much fun that they forgot about the rock. They were happy they had a fun day at the park.<|endoftext|>Once upon a time, there was a little girl named Lily. She loved to play with her toys and her favorite toy was a teddy bear. One day, Lily\'s mommy told'

In [45]:
tokenizer.decode(model.generate(tokenizer.encode("Tim and Lily went to the park. Tim found an interesting rock and gave it to"), 100, temperature=0.01, ablated=True))

'Tim and Lily went to the park. Tim found an interesting rock and gave it to his mom. Tim was very happy and said, "Thank you, Lily. I\'m sorry for being naughty."\n\nFrom that day on, Tim and Lily went home with a big smile on their faces. They were happy and happy to have a fun day.<|endoftext|>Once upon a time, there was a little girl named Lily. She loved to play with her toys and run around in the park. One day, while she was playing, she found a big, red ball. She was'

In [46]:
tokenizer.decode(model.generate(tokenizer.encode("Tim and Lily went to the park. Lily found an interesting rock and gave it to"), 100, temperature=0.01, ablated=True))

'Tim and Lily went to the park. Lily found an interesting rock and gave it to her mom. Her mom was very happy to see the rock and said, "You\'re a good, Lily. You are very good at playing with your rock."\n\nLily and Lily played together every day. They had so much fun that they played together. They had a lot of fun that day.<|endoftext|>Once upon a time, there was a little girl named Lily. She loved to play with her toys and run around in the park. One day, Lily\'s mom asked her to'

In [51]:
prompt_a = tokenizer.encode("Tim and Lily went to the park. Tim found an interesting rock and gave it to")

In [52]:
ret_a = model(torch.tensor(prompt_a).unsqueeze(0).to(device))

In [53]:
ret2_a = model(torch.tensor(prompt_a).unsqueeze(0).to(device), attention_ablations=ret_a["attention_ablations"], neuron_ablations=ret_a["neuron_ablations"])

In [54]:
tokenizer.decode(torch.argmax(ret2_a["logits"],-1)[0,-1:].tolist())

' his'

In [55]:
prompt_b = tokenizer.encode("Tim and Lily went to the park. Lily found an interesting rock and gave it to")

In [56]:
ret_b = model(torch.tensor(prompt_b).unsqueeze(0).to(device))

In [57]:
ret2_b = model(torch.tensor(prompt_b).unsqueeze(0).to(device), attention_ablations=ret_b["attention_ablations"], neuron_ablations=ret_b["neuron_ablations"])

In [58]:
tokenizer.decode(torch.argmax(ret2_b["logits"],-1)[0,-1:].tolist())

' her'

In [65]:
ret2_b = model(torch.tensor(prompt_b).unsqueeze(0).to(device), attention_ablations=ret_a["attention_ablations"], neuron_ablations=ret_a["neuron_ablations"])

In [66]:
tokenizer.decode(torch.argmax(ret2_b["logits"],-1)[0,-1:].tolist())

' her'

In [102]:
ret_a["attention_ablations"][0,:,:,:].transpose(0,1).shape

torch.Size([8, 17, 128])

In [104]:
ret_a["attention_ablations"][0,:,:,:].transpose(0,1).reshape(17*8, 128).shape

torch.Size([136, 128])

In [107]:
px.imshow(ret_a["attention_ablations"][0,:,:,:].transpose(0,1).reshape(17*8, 128).detach().cpu())

In [110]:
ret_a["neuron_ablations"][0,:,:,:].transpose(0,1).reshape(8*17, 512).shape

torch.Size([136, 512])

In [112]:
px.imshow(ret_a["neuron_ablations"][0,:,:,:].transpose(0,1).reshape(8*17, 512).detach().cpu())